In [1]:
%%bash
pip install datasets==1.13.3
pip install transformers==4.11.3
pip install huggingface_hub==0.1
pip install torchaudio
pip install librosa
pip install jiwer

  Using cached datasets-1.13.3-py3-none-any.whl (287 kB)
  Using cached huggingface_hub-0.0.19-py3-none-any.whl (56 kB)


  Attempting uninstall: huggingface-hub


    Found existing installation: huggingface-hub 0.4.0
    Uninstalling huggingface-hub-0.4.0:


ERROR: Could not install packages due to an OSError: [Errno 13] Permission denied: 'INSTALLER'
Consider using the `--user` option or check the permissions.

You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


  Using cached transformers-4.11.3-py3-none-any.whl (2.9 MB)
  Using cached tokenizers-0.10.3-cp38-cp38-manylinux_2_5_x86_64.manylinux1_x86_64.manylinux_2_12_x86_64.manylinux2010_x86_64.whl (3.3 MB)


...

    Found existing installation: huggingface-hub 0.4.0
    Uninstalling huggingface-hub-0.4.0:


ERROR: Could not install packages due to an OSError: [Errno 13] Permission denied: 'INSTALLER'
Consider using the `--user` option or check the permissions.

You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.


In [2]:
from datasets import load_dataset, load_metric, Audio, Dataset
import os
import torchaudio
from tqdm.auto import tqdm

In [ ]:
%%bash 
wget https://www.openslr.org/resources/42/km_kh_male.zip
unzip km_kh_male.zip

--2022-02-02 03:37:28--  https://www.openslr.org/resources/42/km_kh_male.zip
Resolving www.openslr.org (www.openslr.org)... 46.101.158.64
Connecting to www.openslr.org (www.openslr.org)|46.101.158.64|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 866086951 (826M) [application/zip]
Saving to: ‘km_kh_male.zip.1’

     0K .......... .......... .......... .......... ..........  0%  281K 50m9s
    50K .......... .......... .......... .......... ..........  0%  562K 37m38s
   100K .......... .......... .......... .......... ..........  0%  559K 33m29s
   150K .......... .......... .......... .......... ..........  0%  560K 31m24s
   200K .......... .......... .......... .......... ..........  0%  281K 35m8s
   250K .......... .......... .......... .......... ..........  0%  563K 33m27s
   300K .......... .......... .......... .......... ..........  0%  562K 32m15s
   350K .......... .......... .......... .......... ..........  0%  559K 31m22s
   400K .......... ...

In [3]:
from sklearn.model_selection import train_test_split
import pandas as pd
from datasets import load_dataset

colnames=['path','drop','text'] 
df  = pd.read_csv('km_kh_male/line_index.tsv',sep='\t',header=None,names=colnames)
df['path'] = '/workspace/xls-r-300m-km/km_kh_male/wavs/'+df['path'] +'.wav'

train, test = train_test_split(df, test_size=0.1)

train.to_csv('./km_kh_male/line_index_train.csv')
test.to_csv('./km_kh_male/line_index_test.csv')

In [32]:
common_voice_train = load_dataset('csv', data_files='km_kh_male/line_index_train.csv', split= 'train')
common_voice_test = load_dataset('csv', data_files='km_kh_male/line_index_test.csv', split = 'train')

Using custom data configuration default-217f48c3bbd91dba
Reusing dataset csv (/workspace/.cache/huggingface/datasets/csv/default-217f48c3bbd91dba/0.0.0/6b9057d9e23d9d8a2f05b985917a0da84d70c5dae3d22ddd8a3f22fb01c69d9e)
Using custom data configuration default-b7fdb19422ec70d7
Reusing dataset csv (/workspace/.cache/huggingface/datasets/csv/default-b7fdb19422ec70d7/0.0.0/6b9057d9e23d9d8a2f05b985917a0da84d70c5dae3d22ddd8a3f22fb01c69d9e)


In [33]:
common_voice_train = (common_voice_train
                      .remove_columns(["Unnamed: 0", "drop"])
                      .rename_column('text', 'sentence'))
common_voice_test  = (common_voice_test
                      .remove_columns(["Unnamed: 0", "drop"])
                      .rename_column('text', 'sentence'))

In [6]:
# Remove character
import re
chars_to_remove_regex = '[\,\?\.\!\-\;\:\"\“\%\‘\”\�\']'

def remove_special_characters(batch):
    batch["sentence"] = re.sub(chars_to_remove_regex, '', batch["sentence"])
    return batch

In [7]:
# TODO: somehow this break thigns. WHY?
# common_voice_train = common_voice_train.map(remove_special_characters, num_proc=16)
# common_voice_test = common_voice_test.map(remove_special_characters, num_proc=16)

In [8]:
common_voice_train[0]

{'path': '/workspace/xls-r-300m-km/km_kh_male/wavs/khm_3154_3268842134.wav',
 'sentence': 'ការិយាល័យ ប្រឆាំង ការ ជួញដូរ គ្រឿង ញៀន'}

In [9]:
# Build Character

In [34]:
vocab_train = []
vocab_test  = []

for batch in tqdm(common_voice_train):
    sentence = batch['sentence']
    vocab_train.extend(list(set(list(sentence))))
    
for batch in tqdm(common_voice_test):
    sentence = batch['sentence']
    vocab_test.extend(list(set(list(sentence))))

  0%|          | 0/2615 [00:00<?, ?it/s]

  0%|          | 0/291 [00:00<?, ?it/s]

In [35]:
vocab_list = list(set(vocab_train) | set(vocab_test))
vocab_dict = {v: k for k, v in enumerate(sorted(vocab_list))}

In [36]:
print(vocab_dict)

{' ': 0, 'ក': 1, 'ខ': 2, 'គ': 3, 'ឃ': 4, 'ង': 5, 'ច': 6, 'ឆ': 7, 'ជ': 8, 'ឈ': 9, 'ញ': 10, 'ដ': 11, 'ឋ': 12, 'ឌ': 13, 'ឍ': 14, 'ណ': 15, 'ត': 16, 'ថ': 17, 'ទ': 18, 'ធ': 19, 'ន': 20, 'ប': 21, 'ផ': 22, 'ព': 23, 'ភ': 24, 'ម': 25, 'យ': 26, 'រ': 27, 'ល': 28, 'វ': 29, 'ស': 30, 'ហ': 31, 'ឡ': 32, 'អ': 33, 'ឥ': 34, 'ឧ': 35, 'ឪ': 36, 'ឫ': 37, 'ឬ': 38, 'ឭ': 39, 'ឮ': 40, 'ឯ': 41, 'ឱ': 42, 'ា': 43, 'ិ': 44, 'ី': 45, 'ឹ': 46, 'ឺ': 47, 'ុ': 48, 'ូ': 49, 'ួ': 50, 'ើ': 51, 'ឿ': 52, 'ៀ': 53, 'េ': 54, 'ែ': 55, 'ៃ': 56, 'ោ': 57, 'ៅ': 58, 'ំ': 59, 'ះ': 60, 'ៈ': 61, '៉': 62, '៊': 63, '់': 64, '៌': 65, '៍': 66, '៎': 67, '៏': 68, '័': 69, '្': 70}


In [37]:
# make the space more intuitive to understand
vocab_dict["|"] = vocab_dict[" "]
vocab_dict["[UNK]"] = len(vocab_dict)
vocab_dict["[PAD]"] = len(vocab_dict)

del vocab_dict[" "]
len(vocab_dict)

73

In [38]:
import json
with open('vocab.json', 'w') as vocab_file:
    json.dump(vocab_dict, vocab_file)

In [39]:
# Tokenizer

In [40]:
from transformers import Wav2Vec2CTCTokenizer
from transformers import Wav2Vec2FeatureExtractor
from transformers import Wav2Vec2Processor

In [41]:
tokenizer = Wav2Vec2CTCTokenizer.from_pretrained("./", unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")  # './' load vocab.json in the current directory
feature_extractor = Wav2Vec2FeatureExtractor(feature_size=1, sampling_rate=16000, padding_value=0.0, do_normalize=True, return_attention_mask=True)  
processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

file ./config.json not found
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [26]:
def speech_file_to_array_fn(batch):
    audio_array, sampling_rate = torchaudio.load(batch["path"])
    batch["audio"] = {
        "array": audio_array[0].numpy(),
        "path": batch["path"],
        "sampling_rate": sampling_rate
    }
    return batch

In [27]:
common_voice_train = common_voice_train.map(speech_file_to_array_fn)
common_voice_test = common_voice_test.map(speech_file_to_array_fn)

0ex [00:00, ?ex/s]

0ex [00:00, ?ex/s]

In [48]:
common_voice_train = common_voice_train.cast_column("path", Audio(sampling_rate=16_000)).rename_column('path', 'audio')
common_voice_test  = common_voice_test.cast_column("path", Audio(sampling_rate=16_000)).rename_column('path', 'audio')

In [50]:
common_voice_train[0]

{'audio': {'path': '/workspace/xls-r-300m-km/km_kh_male/wavs/khm_3154_3268842134.wav',
  'array': array([ 5.3131345e-07, -1.1117019e-06,  1.9295110e-06, ...,
         -1.5335708e-03, -1.7499180e-03,  0.0000000e+00], dtype=float32),
  'sampling_rate': 16000},
 'sentence': 'ការិយាល័យ ប្រឆាំង ការ ជួញដូរ គ្រឿង ញៀន'}

In [51]:
import IPython.display as ipd
import numpy as np
import random

rand_int = random.randint(0, len(common_voice_train)-1)

print("Target text:", common_voice_train[rand_int]["sentence"])
print("Input array shape:", common_voice_train[rand_int]["audio"]["array"].shape)
print("Sampling rate:", common_voice_train[rand_int]["audio"]["sampling_rate"])
ipd.Audio(data=common_voice_train[rand_int]["audio"]["array"], autoplay=True, rate=16000)

Target text: ចម្រៀង អត្ថាធិប្បាយ ស៊ិន ស៊ីសាមុត
Input array shape: (65536,)
Sampling rate: 16000


In [52]:
# This does not prepare the input for the Transformer model.
# This will resample the data and convert the sentence into indices
# Batch here is just for one entry (row)
def prepare_dataset(batch):
    audio = batch["audio"]
    
    # batched output is "un-batched"
    batch["input_values"] = processor(audio["array"], sampling_rate=audio["sampling_rate"]).input_values[0]
    batch["input_length"] = len(batch["input_values"])
    
    with processor.as_target_processor():
        batch["labels"] = processor(batch["sentence"]).input_ids
    return batch

In [53]:
common_voice_train = common_voice_train.map(prepare_dataset, remove_columns=common_voice_train.column_names, num_proc=16)
common_voice_test = common_voice_test.map(prepare_dataset, remove_columns=common_voice_test.column_names, num_proc=16)

In [41]:
# In case the dataset is too long which can lead to OOM. We should filter them out.
# max_input_length_in_sec = 5.0
# common_voice_train = common_voice_train.filter(lambda x: x < max_input_length_in_sec * processor.feature_extractor.sampling_rate, input_columns=["input_length"])

In [54]:
import torch

from dataclasses import dataclass, field
from typing import Any, Dict, List, Optional, Union

@dataclass
class DataCollatorCTCWithPadding:
    """
    Data collator that will dynamically pad the inputs received.
    Args:
        processor (:class:`~transformers.Wav2Vec2Processor`)
            The processor used for proccessing the data.
        padding (:obj:`bool`, :obj:`str` or :class:`~transformers.tokenization_utils_base.PaddingStrategy`, `optional`, defaults to :obj:`True`):
            Select a strategy to pad the returned sequences (according to the model's padding side and padding index)
            among:
            * :obj:`True` or :obj:`'longest'`: Pad to the longest sequence in the batch (or no padding if only a single
              sequence if provided).
            * :obj:`'max_length'`: Pad to a maximum length specified with the argument :obj:`max_length` or to the
              maximum acceptable input length for the model if that argument is not provided.
            * :obj:`False` or :obj:`'do_not_pad'` (default): No padding (i.e., can output a batch with sequences of
              different lengths).
    """

    processor: Wav2Vec2Processor
    padding: Union[bool, str] = True

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lenghts and need
        # different padding methods
        input_features = [{"input_values": feature["input_values"]} for feature in features]
        label_features = [{"input_ids": feature["labels"]} for feature in features]

        batch = self.processor.pad(
            input_features,
            padding=self.padding,
            return_tensors="pt",
        )
        with self.processor.as_target_processor():
            labels_batch = self.processor.pad(
                label_features,
                padding=self.padding,
                return_tensors="pt",
            )

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        batch["labels"] = labels

        return batch

In [55]:
data_collator = DataCollatorCTCWithPadding(processor=processor, padding=True)

In [56]:
# wer_metric = load_metric("wer")
cer_metric = load_metric("cer")

In [57]:
def compute_metrics(pred):
    pred_logits = pred.predictions
    pred_ids = np.argmax(pred_logits, axis=-1)

    pred.label_ids[pred.label_ids == -100] = processor.tokenizer.pad_token_id

    pred_str = processor.batch_decode(pred_ids)
    # we do not want to group tokens when computing the metrics
    label_str = processor.batch_decode(pred.label_ids, group_tokens=False)

    # wer = wer_metric.compute(predictions=pred_str, references=label_str)
    cer = cer_metric.compute(predictions=pred_str, references=label_str)

    # return {"wer": wer}
    return {"cer": cer}

In [58]:
from transformers import Wav2Vec2ForCTC

model = Wav2Vec2ForCTC.from_pretrained(
    "facebook/wav2vec2-xls-r-300m", 
    attention_dropout=0.0,
    hidden_dropout=0.0,
    feat_proj_dropout=0.0,
    mask_time_prob=0.05,
    layerdrop=0.0,
    ctc_loss_reduction="mean", 
    pad_token_id=processor.tokenizer.pad_token_id,
    vocab_size=len(processor.tokenizer),
)

Some weights of the model checkpoint at facebook/wav2vec2-xls-r-300m were not used when initializing Wav2Vec2ForCTC: ['project_hid.bias', 'quantizer.weight_proj.weight', 'quantizer.weight_proj.bias', 'project_q.weight', 'project_hid.weight', 'quantizer.codevectors', 'project_q.bias']
- This IS expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of Wav2Vec2ForCTC were not initialized from the model checkpoint at facebook/wav2vec2-xls-r-300m and are newly initialized: ['lm_head.weight', 'lm_head.bias']
You should probably TRAIN this model on a down-stream task to be able to use it 

In [59]:
model.freeze_feature_extractor()

/opt/conda/lib/python3.8/site-packages/transformers/models/wav2vec2/modeling_wav2vec2.py:1700: FutureWarning: The method `freeze_feature_extractor` is deprecated and will be removed in Transformers v5.Please use the equivalent `freeze_feature_encoder` method instead.
  warnings.warn(


In [60]:
from transformers import TrainingArguments

training_args = TrainingArguments(
  output_dir='.',
  group_by_length=True,
  per_device_train_batch_size=8,
  gradient_accumulation_steps=2,
  evaluation_strategy="steps",
  gradient_checkpointing=True,
  fp16=True,
  num_train_epochs=30,
  save_steps=100,
  eval_steps=100,
  logging_steps=100,
  learning_rate=3e-5,
  warmup_steps=500,
  save_total_limit=3,
  push_to_hub=True,
)

In [63]:
from transformers import Trainer

trainer = Trainer(
    model=model,
    data_collator=data_collator,
    args=training_args,
    compute_metrics=compute_metrics,
    train_dataset=common_voice_train,
    eval_dataset=common_voice_test,
    tokenizer=processor.feature_extractor,
)

/workspace/xls-r-300m-km/. is already a clone of https://huggingface.co/vitouphy/xls-r-300m-km. Make sure you pull the latest changes with `repo.git_pull()`.
Using amp half precision backend


In [ ]:
trainer.train()

The following columns in the training set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
/opt/conda/lib/python3.8/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use thePyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 2615
  Num Epochs = 30
  Instantaneous batch size per device = 8
  Total train batch size (w. parallel, distributed & accumulation) = 16
  Gradient Accumulation steps = 2
  Total optimization steps = 4890


The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 291
  Batch size = 8
Saving model checkpoint to ./checkpoint-100
Configuration saved in ./checkpoint-100/config.json
